In [1]:
import pandas as pd
import sqlite3
import plotly.express as px

In [2]:
pd.options.display.max_columns = None
pd.options.display.max_rows = None

In [3]:
db = sqlite3.connect('../data/nppes_lite.sqlite') #reopen the connection

query = """
SELECT * 
FROM hop_team
"""
hop_team = pd.read_sql(query,db)

db.close() 

In [4]:
hop_team.head()

from_npi      to_npi  patient_count  transaction_count  average_day_wait  \
0  1033142146  1000000004            491                535            10.232   
1  1013977990  1003000126            134                145            27.352   
2  1013996669  1003000126             91                 92            35.152   
3  1033102504  1003000126             52                 64            15.328   
4  1003029620  1003000126            111                121            33.058   

   std_day_wait  
0        36.558  
1        51.137  
2        68.009  
3        38.300  
4        58.981

In [5]:
hop_team.shape

(31704890, 6)

## 1-Overlaps hop_team with from_npi and to_npi using noSQL query:

In [6]:
db = sqlite3.connect('../data/nppes_lite.sqlite') #reopen the connection

query = """
    SELECT *
    FROM hop_team
    WHERE from_npi IN(
        SELECT DISTINCT(npi)  
        FROM nash_nppes
        WHERE entity_type_code == 1)
    AND to_npi IN(
        SELECT DISTINCT(npi)
        FROM nash_nppes
        WHERE entity_type_code == 2)
"""

hops = pd.read_sql(query,db)

db.close()

In [7]:
hops.shape

(41127, 6)

In [8]:
#save as new table in database called nash_nppes
db = sqlite3.connect('../data/nppes_lite.sqlite') #open connection

hops.to_sql('nash_hop_team', db, if_exists = 'append', index = False) #save nashville hop_team

db.close() #close connection

## 2-Merge nash_nppes and nash_hop_team data using noSQL query:

In [9]:
db = sqlite3.connect('../data/nppes_lite.sqlite') #reopen the connection

query = """
WITH provider AS(
SELECT DISTINCT(npi), first_name || ' ' || last_name AS from_physician , 
        address_1 AS from_address,
        taxonomy_code AS from_tax,
        grouping AS from_grouping,
        classification AS from_classification,
        zip as to_zip
FROM nash_nppes
INNER JOIN nash_hop_team
ON npi = from_npi
),

hospital AS(
SELECT DISTINCT(npi), 
        org_name AS to_facility,
        address_1 AS to_address,
        taxonomy_code AS to_tax,
        grouping AS to_grouping,
        classification AS to_classification,
        zip as from_zip
FROM nash_nppes
INNER JOIN nash_hop_team
ON npi = to_npi
) 

SELECT from_npi, from_physician, from_address, from_zip, from_tax, from_grouping, from_classification, 
       to_npi, to_facility, to_address, to_zip, to_tax, to_grouping, to_classification,
       patient_count, transaction_count, average_day_wait, std_day_wait
        
FROM nash_hop_team
INNER JOIN provider as p
ON p.npi = from_npi
INNER JOIN hospital as h
ON h.npi = to_npi

"""
final = pd.read_sql(query,db)

db.close() 

In [10]:
final.head()

from_npi    from_physician                         from_address from_zip  \
0  1003963976    BENJAMIN HAYES  3098 CAMPBELL STATION PKWY STE A201    37174   
1  1033246640     OUIDA COLLINS                             3601 TVC    37027   
2  1033215157    KENDRA RENNELL                    1224 TROTWOOD AVE    37027   
3  1023223898  RANDALL WOODFORD                    5301 VIRGINIA WAY    37027   
4  1023253549      RHETT BRUNER              1501 WOODLAND POINTE DR    37027   

     from_tax                        from_grouping from_classification  \
0  207NP0225X  Allopathic & Osteopathic Physicians         Dermatology   
1  207Q00000X  Allopathic & Osteopathic Physicians     Family Medicine   
2  174400000X              Other Service Providers          Specialist   
3  207ZP0102X  Allopathic & Osteopathic Physicians           Pathology   
4  111N00000X               Chiropractic Providers        Chiropractor   

       to_npi                   to_facility                 to_address to_zip  \
0  1003028770   SPRING HILL DERMATOLOGY PLC          1229 RESERVE BLVD  37174   
1  1003863580  ASSOCIATED PATHOLOGISTS, LLC  5301 VIRGINIA WAY STE 300  37232   
2  1003863580  ASSOCIATED PATHOLOGISTS, LLC  5301 VIRGINIA WAY STE 300  38401   
3  1003863580  ASSOCIATED PATHOLOGISTS, LLC  5301 VIRGINIA WAY STE 300  37027   
4  1003863580  ASSOCIATED PATHOLOGISTS, LLC  5301 VIRGINIA WAY STE 300  37214   

       to_tax                          to_grouping to_classification  \
0  207N00000X  Allopathic & Osteopathic Physicians       Dermatology   
1  207ZP0102X  Allopathic & Osteopathic Physicians         Pathology   
2  207ZP0102X  Allopathic & Osteopathic Physicians         Pathology   
3  207ZP0102X  Allopathic & Osteopathic Physicians         Pathology   
4  207ZP0102X  Allopathic & Osteopathic Physicians         Pathology   

   patient_count  transaction_count  average_day_wait  std_day_wait  
0           2535               3945             0.000         0.000  
1             58                 58            45.603        56.574  
2            124                126            22.833        53.329  
3           1739               1872             0.169         5.185  
4             34                 53            31.887        50.676

In [11]:
final.shape

(41127, 18)

In [13]:
#save as new table in database called nash_nppes_hop_team
db = sqlite3.connect('../data/nppes_lite.sqlite') #open connection

final.to_sql('nash_nppes_hop_team', db, if_exists = 'append', index = False) #save nashville hop_team

db.close() #close connection

## 3-Cleaner data from Courtney:

In [ ]:
#nash_referrals = pd.read_csv('../data/nash_referrals.csv')
#nash_referrals.head()

In [ ]:
#nash_referrals.shape

In [ ]:
#save as new table in database called nash_referrals
#db = sqlite3.connect('../data/nppes_lite.sqlite') #open connection

#nash_referrals.to_sql('nash_referrals', db, if_exists = 'append', index = False) #save nashville hop_team

#db.close() #close connection

## 4-Final cleaning:

After several discussion with my classmates we decides to use only "General Acute Care Hospital" from "to_npi_specialty" columns.

**Final cleaned file used by the entire class:**

In [46]:
### Load the final csv file used to answer the questions for BlueBook Healthcare
nash_referrals_mini = pd.read_csv('../data/nashville_referrals_normalised_only_hospitals_any_avg_day_wait.csv')
nash_referrals_mini

Unnamed: 0     index    from_npi      to_npi  patient_count  \
0              0    615039  1013179860  1417938846             71   
1              1   3024235  1336126887  1417938846             55   
2              2   3024236  1336230424  1417938846             38   
3              3   3024237  1346288966  1417938846            146   
4              4   3024244  1326086653  1417938846             43   
5              5   4931236  1508935776  1417938846            330   
6              6   4931237  1508916586  1417938846             96   
7              7   6269382  1366817611  1417938846            146   
8              8   7627700  1053366369  1417938846            379   
9              9   9058193  1104837327  1417938846             52   
10            10   9058195  1104933738  1417938846            506   
11            11   9058196  1104890003  1417938846             67   
12            12   9058197  1114074085  1417938846            340   
13            13  10158217  1750584710  1417938846            126   
14            14  10158218  1740326495  1417938846            294   
15            15  10158220  1730114315  1417938846             47   
16            16  11431014  1437107265  1417938846             33   
17            17  11431016  1427162619  1417938846            124   
18            18  11431017  1407836356  1417938846            208   
19            19  11431018  1407090236  1417938846             63   
20            20  11431019  1447366075  1417938846            108   
21            21  11431020  1447307251  1417938846             46   
22            22  12840986  1447625892  1417938846            157   
23            23  12840988  1487021663  1417938846             91   
24            24  12840989  1467483164  1417938846             93   
25            25  13911661  1902823099  1417938846            100   
26            26  13911662  1891780896  1417938846             29   
27            27  13911663  1891861506  1417938846             70   
28            28  13911664  1902015019  1417938846             34   
29            29  13911665  1932279429  1417938846             71   
30            30  16236782  1861541351  1417938846            601   
31            31  16236786  1871696096  1417938846             23   
32            32  17936670  1144259631  1417938846             36   
33            33  17936673  1154576825  1417938846             49   
34            34  20378315  1649271206  1417938846            133   
35            35  20378316  1649471780  1417938846            393   
36            36  20902926  1780667006  1417938846            221   
37            37  20902927  1790891315  1417938846            274   
38            38  22320267  1811393788  1417938846             50   
39            39  22320268  1811307036  1417938846            110   
40            40  23679042  1700810371  1417938846             88   
41            41  23679046  1679644769  1417938846             90   
42            42  23679047  1679689285  1417938846            148   
43            43  24502675  1235121179  1417938846             41   
44            44  25893612  1275536468  1417938846            186   
45            45  25893613  1285843896  1417938846             24   
46            46  25893615  1275888992  1417938846            182   
47            47  25893616  1285615278  1417938846             65   
48            48  26581604  1942642152  1417938846             55   
49            49  27621541  1992956114  1417938846             35   
50            50  28772912  1538590070  1417938846             91   
51            51  28772915  1558355941  1417938846             99   
52            52  28772917  1558797415  1417938846             62   
53            53  30515978  1205826526  1417938846            576   
54            54  30515979  1194875179  1417938846            179   
55            55  30515980  1215211677  1417938846             40   
56            56  30515981  1225027014  1417938846            172   
57  

In [47]:
### Keep only the npis from that file to merge it with mine so I have more information like zipcodes
nash_referrals_mini = nash_referrals_mini[["from_npi", "to_npi", "to_facility_name_normalised"]]

In [48]:
### Merge csv file cleaned from the class with my cleaned data
nash_referrals_final_mini = nash_referrals_mini.merge(nash_referrals_final_clean, on=['from_npi', 'to_npi'])

In [49]:
nash_referrals_final_mini.shape

(6425, 12)

In [50]:
nash_referrals_final_mini.head(2)

from_npi      to_npi    to_facility_name_normalised from_physician  \
0  1013179860  1417938846  Macon County General Hospital      GARY YAWN   
1  1336126887  1417938846  Macon County General Hospital    ROBERT WEBB   

                         from_address  from_zip from_classification  \
0  353 NEW SHACKLE ISLAND RD STE 300C     37083   Internal Medicine   
1           353 NEW SHACKLE ISLAND RD     37083             Urology   

                           to_facility         to_address  to_zip  \
0  MACON COUNTY GENERAL HOSPITAL, INC.  204 MEDICAL DRIVE   37075   
1  MACON COUNTY GENERAL HOSPITAL, INC.  204 MEDICAL DRIVE   37075   

             to_classification  patient_count  
0  General Acute Care Hospital             71  
1  General Acute Care Hospital             55

In [51]:
### Save file
nash_referrals_final_mini.to_csv('../data/nash_referrals_final_mini.csv', index=False)

## 5-Previous cleaning and EDA not used in the final file used for the presentation and to answer the questions.

In [ ]:
db = sqlite3.connect('../data/nppes_lite.sqlite') #reopen the connection

query = """
SELECT * 
FROM nash_nppes_hop_team
"""
nash_nppes_hop_team = pd.read_sql(query,db)

db.close() 

In [ ]:
nash_nppes_hop_team.to_csv('../data/nash_referrals_final.csv')

In [ ]:
nash_referrals_final_clean = pd.read_csv('../data/nash_referrals_final.csv')

In [ ]:
### Clean columns
nash_referrals_final_clean = nash_referrals_final_clean.drop(columns = ["Unnamed: 0", "from_tax", "from_grouping", "to_tax", "to_grouping", "transaction_count", "average_day_wait", "std_day_wait"])

In [ ]:
nash_referrals_final_clean.shape

In [ ]:
### Save file
#nash_referrals_final_clean.to_csv('../data/nash_referrals_final_clean.csv', index=False)

### A-Classification from hospital cleaning (not used in the final file cleaned):

In [ ]:
#nash_referrals_final.to_classification.value_counts()

In [ ]:
#define a list of elements we want to remove from the to_classification column
exclude_to_classification = ["Radiology", 
                             "Anesthesiology", 
                             "Ambulance", 
                             "Emergency Medicine", 
                             "Pathology", 
                             "Durable Medical Equipment & Medical Supplies", 
                             "Clinical Medical Laboratory", 
                             "Portable X-ray and/or Other Portable Diagnostic Imaging Supplier", 
                             "Pharmacy", 
                             "Audiologist-Hearing Aid Fitter", 
                             "Prosthetic/Orthotic Supplier", 
                             "Eyewear Supplier", 
                             "Preferred Provider Organization"]
#use boolean mask to say 'keep everything that is NOT included in this list'
nash_referrals_final = nash_referrals_final[~nash_referrals_final.to_classification.isin(exclude_to_classification)]
nash_referrals_final.info()  

In [ ]:
### Remove values if from_classification is the same as to_classification
#nash_referrals_final = nash_referrals_final[nash_referrals_final.from_classification != nash_referrals_final.to_classification]
#nash_referrals_final.shape

### B-Look at interaction physician and hospital where average waiting time = 0, which most likely mean physician work in this specific hospital:

In [ ]:
#no_wait = nash_referrals[nash_referrals.average_day_wait < 1]

In [ ]:
#no_wait_neo4j = no_wait[['from_physician', 'to_facility', 'patient_count']]

In [ ]:
### Save file
#no_wait_neo4j.to_csv('../data/nowait.csv', index=False)

In [ ]:
#fig = px.scatter(no_wait, x="from_physician", y="patient_count",
#        color="to_facility",
#        title=" ")
#fig.update(layout_showlegend=False)
#fig.show()

In [ ]:
#no_wait.to_facility.value_counts()

In [ ]:
#define a list of elements we want to keep from the to_facility column
#keep_to_facility = ["VANDERBILT UNIVERSITY MEDICAL CENTER", 
#                             "SAINT THOMAS MEDICAL PARTNERS", 
#                             "TENNESSEE ORTHOPAEDIC ALLIANCE PA", 
#                             "HERITAGE MEDICAL ASSOCIATES PC", 
#                             "MURFREESBORO MEDICAL CLINIC", 
#                             "TENNESSEE ONCOLOGY PLLC", 
#                             "MAURY REGIONAL MEDICAL GROUP, INC", 
#                             "HCA HEALTH SERVICES OF TENNESSEE, INC.", 
#                             "UROLOGY ASSOCIATES PC", 
#                             "THE LITTLE CLINIC OF TENNESSEE LLC", 
#                             "CENTERSTONE OF TENNESSEE, INC.", 
#                             "PREMIER ORTHOPAEDICS & SPORTS MEDICINE PLC", 
#                             "CENTENNIAL HEART LLC",
#                             "NEPHROLOGY ASSOCIATES, PC",
#                             "VANDERBILT HEALTH AND WILLIAMSON MEDICAL CENTER CLINICS AND SERVICES,",
#                             "NASHVILLE ANESTHESIA PLLC",
#                             "PAIN MANAGEMENT GROUP, P.C.",
#                   ]
#use boolean mask to say 'keep everything that is NOT included in this list'
#keep_to_facility_no_wait = no_wait[no_wait.to_facility.isin(keep_to_facility)]
#keep_to_facility_no_wait.info() 

In [ ]:
#fig = px.scatter(keep_to_facility_no_wait, x="from_physician", y="patient_count",
#        color="to_facility",
#        title=" ")
#fig.update(layout_showlegend=False)
#fig.show()

### C-Look at referals with averge time wait over a day:

In [ ]:
#wait_over_2_day = nash_referrals[nash_referrals.average_day_wait >= 2]

In [ ]:
#wait_over_2_day.shape

In [ ]:
#wait_over_1_day.head()

In [ ]:
### Remove values if from_classification is the same as to_classification
#wait_over_1_day = wait_over_1_day[wait_over_1_day.from_classification != wait_over_1_day.to_classification]
#wait_over_1_day.shape

In [ ]:
#wait_over_1_day.head()

In [ ]:
#fig = px.scatter(wait_over_1_day, x="to_facility", y="patient_count",
#        color="from_classification",
#        title=" ")
#fig.update(layout_showlegend=False)
#fig.show()

In [ ]:
#wait_over_1_day.groupby(['to_facility', 'from_classification'])[ "patient_count"].sum().reset_index()

In [ ]:
#fig = px.scatter(wait_over_1_day.groupby(['to_facility', 'from_classification'])[ "patient_count"].sum().reset_index(), x="to_facility", y="patient_count",
#        color= "from_classification",
#        title=" ")
#fig.update(layout_showlegend=False)
#fig.show()

In [ ]:
#wait = wait_over_1_day[['from_physician', 'to_facility', 'patient_count']]

In [ ]:
#wait = wait.dropna(axis=0)

In [ ]:
### Save file
#wait.to_csv('../data/wait.csv', index=False)